# Capstone Project Analysis

### Set up notebook

In [7]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!pip install folium
import folium # map rendering library

!pip install foursquare
import foursquare

!conda install -c conda-forge basemap-data-hires=1.0.8.dev0
from mpl_toolkits.basemap import Basemap

import matplotlib.pyplot as plt

print('Libraries imported.')

Solving environment: done

# All requested packages already installed.



KeyError: 'PROJ_LIB'

In [9]:
#from mpl_toolkits.basemap import Basemap

import matplotlib.pyplot as plt

### Import UK postcodes

In [18]:
#!wget -O London_postcodes.csv https://www.doogal.co.uk/UKPostcodesCSV.ashx?area=London

--2020-02-26 10:34:24--  https://www.doogal.co.uk/UKPostcodesCSV.ashx?area=London
Resolving www.doogal.co.uk (www.doogal.co.uk)... 109.228.61.150
Connecting to www.doogal.co.uk (www.doogal.co.uk)|109.228.61.150|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [text/plain]
Saving to: ‘London_postcodes.csv’

    [   <=>                                 ] 147,962,013 9.58MB/s   in 16s    

2020-02-26 10:34:44 (8.64 MB/s) - ‘London_postcodes.csv’ saved [147962013]



Import the first containing the postcodes in London.

This file also contains the area names, longitude and latidude for each postcode.

Source: https://www.doogal.co.uk/london_postcodes.php

In [19]:
# Import data
df_areas_all = pd.read_csv('London_postcodes.csv')
df_areas = df_areas_all[['Postcode', 'Latitude', 'Longitude', 'District']]

# Reformat columns
new_columns = ['Postcode', 'Latitude', 'Longitude', 'Area']
df_areas.columns = new_columns

df_areas.head()

Postcode   Latitude  Longitude     Area
0  BR1 1AA  51.401546   0.015415  Bromley
1  BR1 1AB  51.406333   0.015208  Bromley
2  BR1 1AD  51.400057   0.016715  Bromley
3  BR1 1AE  51.404543   0.014195  Bromley
4  BR1 1AF  51.401392   0.014948  Bromley

In [20]:
# Group longitude and latitude 
df_areas_grouped = df_areas.groupby(df_areas['Area'])

aggregator = {'Latitude':'mean', 'Longitude':'mean'}

df_London_areas = df_areas_grouped.agg(aggregator)

# Reformat the table
df_London_areas = df_London_areas.reset_index()

# Convert to Dictionary
dict_London_areas = df_London_areas.transpose().to_dict()

# Using the  Foursquare API

Define Foursquare Credentials and Version.

This function connects to Foursquare using the Foursquare python librairy listed here: https://developer.foursquare.com/docs/api/libraries

Further details can be found here: https://pypi.python.org/pypi/foursquare

In [21]:
# Define credentials
# Construct the client object
client = foursquare.Foursquare(client_id='BV3CGSM43ONE0N2TUKXVKUMAVISA4PH2QGF1MTMQMOGFE0ZZ', 
                               client_secret='0G15UOUUAOUF0OZRR3Q01XERKX1XIUQCRQXWDKP13LTAE1L0', 
                               redirect_uri='http://fondu.com/oauth/authorize')

# Build the authorization url for your app
auth_uri = client.oauth.auth_url()

Define function to retrieve different types of venues in an area

In [22]:
def get_venues(dictionary, categoryId, category):
    
    venues_loc_info = [] 
    venues_cat_info = []

    for london_area in dictionary:
        
        # Define Area
        area = dict_London_areas[london_area]

        area_name = str(area ['Area'])

        # Latitude and Longitude for the area
        lat_string = str(area ['Latitude'])
        long_string = str(area ['Longitude'])

        lat_long = lat_string + ',' + long_string

        # Call the foursquare API
        test_data = client.venues.search(params={'ll': lat_long , 
                                                 'intent': 'browse' , 
                                                 'radius': 10000 , 
                                                 'limit': 100,
                                                 'categoryId': categoryId})

        test_venues = pd.DataFrame(test_data['venues'])
        
        if  len(test_venues) != 0 : 

        
            # Define Catgories 
            test_categories = dict(test_venues['categories'])

            # Define locations
            test_locations = dict(test_venues['location'])


            for i in test_categories :

                venue_cat = test_categories[i] 

                if len(venue_cat) != 0 :
                    venue_cat_df = pd.DataFrame(venue_cat)
                    venue = venue_cat_df['id'].astype('str')
                    cat = venue_cat_df['name'].astype('str')
                    venues_cat_info.append([area_name, cat[0], venue[0]])

                else:
                    venue = 'unknown'
                    cat = 'unknown'
                    venues_cat_info.append([area_name, cat, venue])



            for i in test_locations :
                venue_loc = test_locations[i]
                lat = venue_loc['lat']
                long = venue_loc['lng']
                venues_loc_info.append([lat, long])


            df_venues_cat = pd.DataFrame(venues_cat_info)
            df_venues_loc = pd.DataFrame(venues_loc_info)

            df_venues_merge = pd.merge(df_venues_cat,df_venues_loc,left_index=True ,right_index=True)


            # Create Dataframe
            df_venues = df_venues_merge.drop_duplicates(keep = 'first')
            df_venues_cols = df_venues.rename(columns = { '0_x' : 'Area', '1_x': 'Venue Type', 2: 'ID', '0_y' : 'Latitude', '1_y' : 'Longitude'})
            df_venues_cols['Type'] = category

            # Remove blank values
            df_venues_final = df_venues_cols[df_venues_cols['Venue Type'] != 'unknown']


    return df_venues_final
    
    

Use the function to find different types of venue

In [23]:
df_venues_food = get_venues(dict_London_areas,'4d4b7105d754a06374d81259', 'Resturant/Food')

df_venues_food.head()

Area      Venue Type                        ID   Latitude  \
0  Barking and Dagenham     Coffee Shop  4bf58dd8d48988d1e0931735  51.514415   
1  Barking and Dagenham  Sandwich Place  4bf58dd8d48988d1c5941735  51.500255   
2  Barking and Dagenham            Café  4bf58dd8d48988d16d941735  51.543535   
3  Barking and Dagenham     Coffee Shop  4bf58dd8d48988d1e0931735  51.490376   
4  Barking and Dagenham     Coffee Shop  4bf58dd8d48988d1e0931735  51.508128   

   Longitude            Type  
0   0.008015  Resturant/Food  
1   0.003513  Resturant/Food  
2  -0.008982  Resturant/Food  
3   0.069298  Resturant/Food  
4   0.031543  Resturant/Food

In [24]:
df_venues_entertainment = get_venues(dict_London_areas,'4d4b7104d754a06370d81259', 'Entertainment')

df_venues_entertainment.head()

Area   Venue Type                        ID   Latitude  \
0  Barking and Dagenham  Music Venue  4bf58dd8d48988d1e5931735  51.502827   
1  Barking and Dagenham      Stadium  4bf58dd8d48988d184941735  51.538628   
2  Barking and Dagenham    Multiplex  4bf58dd8d48988d180941735  51.543526   
3  Barking and Dagenham    Multiplex  4bf58dd8d48988d180941735  51.502950   
4  Barking and Dagenham  Music Venue  4bf58dd8d48988d1e5931735  51.502672   

   Longitude           Type  
0   0.003182  Entertainment  
1  -0.016565  Entertainment  
2  -0.006512  Entertainment  
3   0.005063  Entertainment  
4   0.003152  Entertainment

In [25]:
df_venues_night_life = get_venues(dict_London_areas,'4d4b7105d754a06376d81259', 'Night Life')

df_venues_night_life.head()

Area Venue Type                        ID   Latitude  \
0  Barking and Dagenham        Bar  4bf58dd8d48988d116941735  51.504177   
1  Barking and Dagenham        Pub  4bf58dd8d48988d11b941735  51.492536   
2  Barking and Dagenham        Pub  4bf58dd8d48988d11b941735  51.508796   
3  Barking and Dagenham        Pub  4bf58dd8d48988d11b941735  51.492363   
4  Barking and Dagenham        Pub  4bf58dd8d48988d11b941735  51.491960   

   Longitude        Type  
0   0.049773  Night Life  
1   0.069904  Night Life  
2   0.025127  Night Life  
3   0.071665  Night Life  
4   0.069186  Night Life

In [26]:
df_venues_office = get_venues(dict_London_areas,'4bf58dd8d48988d124941735', 'Office')

df_venues_office.head()

Area           Venue Type                        ID  \
0  Barking and Dagenham               Office  4bf58dd8d48988d124941735   
1  Barking and Dagenham               Office  4bf58dd8d48988d124941735   
2  Barking and Dagenham  Government Building  4bf58dd8d48988d126941735   
3  Barking and Dagenham               Office  4bf58dd8d48988d124941735   
4  Barking and Dagenham               Office  4bf58dd8d48988d124941735   

    Latitude  Longitude    Type  
0  51.542148  -0.009446  Office  
1  51.543128  -0.004146  Office  
2  51.541860  -0.008627  Office  
3  51.543170  -0.004039  Office  
4  51.494587   0.167441  Office

In [27]:
df_venues_shops = get_venues(dict_London_areas,'4d4b7105d754a06378d81259', 'Shops')

df_venues_shops.head()

Area              Venue Type                        ID  \
0  Barking and Dagenham           Shopping Mall  4bf58dd8d48988d1fd941735   
1  Barking and Dagenham          Shopping Plaza  5744ccdfe4b0c0459246b4dc   
2  Barking and Dagenham          Shopping Plaza  5744ccdfe4b0c0459246b4dc   
3  Barking and Dagenham           Shopping Mall  4bf58dd8d48988d1fd941735   
4  Barking and Dagenham  Furniture / Home Store  4bf58dd8d48988d1f8941735   

    Latitude  Longitude   Type  
0  51.542892  -0.006909  Shops  
1  51.489446   0.013595  Shops  
2  51.556145  -0.008739  Shops  
3  51.541493  -0.001190  Shops  
4  51.489348   0.016108  Shops

In [28]:
df_venues_veg = get_venues(dict_London_areas,'4bf58dd8d48988d1d3941735', 'Vegetarian/Vegan')

df_venues_veg.head()

Area                     Venue Type  \
0  Barking and Dagenham  Vegetarian / Vegan Restaurant   
1  Barking and Dagenham          Vietnamese Restaurant   
2  Barking and Dagenham              Indian Restaurant   
3  Barking and Dagenham  Vegetarian / Vegan Restaurant   
4  Barking and Dagenham  Vegetarian / Vegan Restaurant   

                         ID   Latitude  Longitude              Type  
0  4bf58dd8d48988d1d3941735  51.508134   0.032315  Vegetarian/Vegan  
1  4bf58dd8d48988d14a941735  51.542975  -0.006375  Vegetarian/Vegan  
2  4bf58dd8d48988d10f941735  51.542572   0.050107  Vegetarian/Vegan  
3  4bf58dd8d48988d1d3941735  51.502040   0.004176  Vegetarian/Vegan  
4  4bf58dd8d48988d1d3941735  51.547215  -0.010912  Vegetarian/Vegan

In [29]:
df_venues = df_venues_entertainment.append([df_venues_night_life, df_venues_office, df_venues_shops, df_venues_food, df_venues_veg])

df_venues = df_venues.reset_index(drop = True)

df_venues = df_venues.drop_duplicates(keep = 'first')

df_venues.head()

Area   Venue Type                        ID   Latitude  \
0  Barking and Dagenham  Music Venue  4bf58dd8d48988d1e5931735  51.502827   
1  Barking and Dagenham      Stadium  4bf58dd8d48988d184941735  51.538628   
2  Barking and Dagenham    Multiplex  4bf58dd8d48988d180941735  51.543526   
3  Barking and Dagenham    Multiplex  4bf58dd8d48988d180941735  51.502950   
4  Barking and Dagenham  Music Venue  4bf58dd8d48988d1e5931735  51.502672   

   Longitude           Type  
0   0.003182  Entertainment  
1  -0.016565  Entertainment  
2  -0.006512  Entertainment  
3   0.005063  Entertainment  
4   0.003152  Entertainment

# Visualising the data on the map

In [30]:
# create map of London using latitude and longitude values
map_london = folium.Map(location=[51.5074, -0.1], zoom_start=10,  tiles = "Stamen Toner")


# Select resturants
df_food = df_venues[df_venues['Type'] == 'Resturant/Food']

# add markers to map
for lat, lng, Type in zip(df_food['Latitude'], df_food['Longitude'], df_food['Type']):
    
    folium.CircleMarker(
        [lat, lng],
        radius=2,
        color='red',
        fill=True,
        fill_opacity=0.7).add_to(map_london)  
    
map_london

In [31]:
df_veg = df_venues[df_venues['Type'] == 'Vegetarian/Vegan']


# add markers to map
for lat, lng, Type in zip(df_veg['Latitude'], df_veg['Longitude'], df_veg['Type']):
    
    folium.CircleMarker(
        [lat, lng],
        radius=2,
        color='blue',
        fill=True,
        fill_opacity=0.7).add_to(map_london)  
    
map_london


In [32]:
df_entertainment = df_venues[df_venues['Type'] == 'Night Life']


# add markers to map
for lat, lng, Type in zip(df_entertainment['Latitude'], df_entertainment['Longitude'], df_entertainment['Type']):
    
    folium.CircleMarker(
        [lat, lng],
        radius=2,
        color='green',
        fill=True,
        #fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_london)  
    
map_london

In [33]:
df_shops = df_venues[df_venues['Type'] == 'Shops']


# add markers to map
for lat, lng, Type in zip(df_shops['Latitude'], df_shops['Longitude'], df_shops['Type']):
    
    folium.CircleMarker(
        [lat, lng],
        radius=2,
        color='green',
        fill=True,
        #fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_london)  
    
map_london


In [34]:
# create map of London using latitude and longitude values
map_london_veg = folium.Map(location=[51.5074, -0.1], zoom_start=10,  tiles = "Stamen Toner")

df_veg = df_venues[df_venues['Type'] == 'Vegetarian/Vegan']


# add markers to map
for lat, lng, Type in zip(df_veg['Latitude'], df_veg['Longitude'], df_veg['Type']):
    
    folium.CircleMarker(
        [lat, lng],
        radius=2,
        color='red',
        fill=True,
        fill_opacity=0.7).add_to(map_london_veg)  
    
map_london_veg
